In [1]:
import json
import pandas as pd
import requests
import time
import warnings

from tqdm import tqdm
from datetime import datetime
from meteostat import Hourly, Point

warnings.filterwarnings('ignore')

## Получение и обработка данных о границах районов

### Источник данных
**Источник:** [Overpass Turbo](https://overpass-turbo.eu/)

---
### Запрос на границы районов Москвы
```overpass
[out:json];
area[name="Москва"]->.boundary;
(
  relation["boundary"="administrative"]["admin_level"="8"](area.boundary);
);
out geom;
```

Выполняем запрос, затем делаем экспорт данных как GeoJSON, вручную меняем название на export_borders.geojson, сохраняем в рабочую директорию

In [656]:
path_borders = 'https://raw.githubusercontent.com/RuslanDavletov/Analysis-of-taxi-demand/main/data/export_borders.geojson'
path_centers = 'https://raw.githubusercontent.com/RuslanDavletov/Analysis-of-taxi-demand/main/data/export_centers.geojson'
path_stations = "https://raw.githubusercontent.com/RuslanDavletov/Analysis-of-taxi-demand/main/data/station_load_data_res%20(1).csv"

In [646]:
response = requests.get(path_borders)
data = response.json()

In [648]:
data

{'type': 'FeatureCollection',
 'generator': 'overpass-turbo',
 'copyright': 'The data included in this document is from www.openstreetmap.org. The data is made available under ODbL.',
 'timestamp': '2025-02-16T08:08:58Z',
 'features': [{'type': 'Feature',
   'properties': {'@id': 'relation/226927',
    'addr:country': 'RU',
    'addr:region': 'Москва',
    'admin_level': '8',
    'alt_name': 'муниципальный округ Кунцево',
    'boundary': 'administrative',
    'description': 'район — административно-территориальная единица; муниципальный округ — тип муниципального образования (с 1 июля 2012)',
    'name': 'район Кунцево',
    'name:ca': 'Districte de Kúntsevo',
    'name:en': 'Kuntsevo District',
    'name:ru': 'район Кунцево',
    'name:uk': 'Район Кунцеве',
    'official_status': 'ru:внутригородская территория города федерального значения',
    'type': 'boundary',
    'wikidata': 'Q155102',
    'wikipedia': 'ru:Кунцево (район Москвы)'},
   'geometry': {'type': 'MultiPolygon',
    'coo

In [650]:
data_district = []

# Перебираем районы
for feature in data['features']:
    properties = feature['properties']
    geometry = feature['geometry']

    if geometry['type'] == 'MultiPolygon':
        for polygon in geometry['coordinates']:
            coords = [{'lng': point[0], 'lat': point[1]} for point in polygon[0]]
            district = {
                "type": "Polygon",
                "coordinates": [coords],
                "name": properties.get('name', 'Без названия'),
                "id": properties.get('@id', 'Неизвестно')
            }
            data_district.append(district)

    elif geometry['type'] == 'Polygon':
        coords = [{'lng': point[0], 'lat': point[1]} for point in geometry['coordinates'][0]]
        district = {
            "type": "Polygon",
            "coordinates": [coords],
            "name": properties.get('name', 'Без названия'),
            "id": properties.get('@id', 'Неизвестно')
        }
        data_district.append(district)


In [652]:
data_district

[{'type': 'Polygon',
  'coordinates': [[{'lng': 37.3786411, 'lat': 55.8083657},
    {'lng': 37.3793519, 'lat': 55.8091719},
    {'lng': 37.3804959, 'lat': 55.8090228},
    {'lng': 37.3806199, 'lat': 55.8093712},
    {'lng': 37.3849555, 'lat': 55.8090616},
    {'lng': 37.3850513, 'lat': 55.8093072},
    {'lng': 37.3823725, 'lat': 55.8095241},
    {'lng': 37.3807281, 'lat': 55.8096574},
    {'lng': 37.3810808, 'lat': 55.8106454},
    {'lng': 37.3808179, 'lat': 55.8106867},
    {'lng': 37.3796746, 'lat': 55.8106902},
    {'lng': 37.3800894, 'lat': 55.8111232},
    {'lng': 37.380221, 'lat': 55.8112671},
    {'lng': 37.3801967, 'lat': 55.8113191},
    {'lng': 37.3797576, 'lat': 55.8114726},
    {'lng': 37.379704, 'lat': 55.8114913},
    {'lng': 37.3794286, 'lat': 55.8115783},
    {'lng': 37.379299, 'lat': 55.8116193},
    {'lng': 37.3792076, 'lat': 55.8116482},
    {'lng': 37.3791905, 'lat': 55.8116582},
    {'lng': 37.3789377, 'lat': 55.8118067},
    {'lng': 37.3787066, 'lat': 55.8119424},

## Получение данных о поездках в такси и каршеринге через API

Источник - https://prodvizhenie.mos.ru

In [16]:
url = 'https://prodvizhenie.mos.ru/api/graphql'  

headers = {
    'Content-Type': 'application/json',
    'User-Agent': 'Mozilla/5.0',
}

query = """
query GeometryStatsMapTooltip(
  $customGeometry: [[[Point!]]], 
  $filter: Filter!, 
  $source: DataSourceType!, 
  $eventType: EventType!
) {
  currentPeriod: ridePolygonStats(
    ids: []
    customGeometry: $customGeometry
    filter: $filter
    source: $source
    aggregation: GEOMETRY
    eventType: $eventType
  ) {
    totalRideCount
    data {
      date
      hour
      rideCount
      __typename
    }
    __typename
  }
}
"""

In [18]:
def get_taxi_data(fromDate, toDate, coords, source, eventType):
    variables = {
        "filter": {
            "fromDate": fromDate,
            "toDate": toDate,
            "hours": [0, 23],
            "weekdays": [1, 2, 3, 4, 5, 6, 7]
        },
        "customGeometry": [coords],
        "source": f"{source}",
        "eventType": f"{eventType}"
    }

    response = requests.post(url, json={'query': query, 'variables': variables}, headers=headers)
    data = response.json()

    # Оставляем только полезные данные
    result = data.get('data', {}).get('currentPeriod', {})
    return {
        "totalRideCount": result.get('totalRideCount', 0),
        "rides": result.get('data', [])
    }

In [20]:
def get_df(start_date, end_date, source, event):
    main_df = pd.DataFrame()
    
    for i in tqdm(range(len(data_district)), desc="Обработка районов"):
        coords = data_district[i]['coordinates']
        get_json = get_taxi_data(start_date, end_date, coords, source, event)
        
        # Преобразование в DataFrame
        df = pd.DataFrame(get_json["rides"])
        
        # Добавим столбцы с информацией о районе
        df['district_name'] = data_district[i]['name']
        df['district_id'] = i
        
        main_df = pd.concat([main_df, df])
        
        # Задержка в 1 секунду
        time.sleep(1)
    return main_df


In [22]:
taxi_start = get_df("2024-01-01", "2025-01-01", 'TAXI', 'START')

Обработка районов: 100%|██████████████████████| 140/140 [08:14<00:00,  3.53s/it]


In [23]:
taxi_finish = get_df("2024-01-01", "2025-01-01", 'TAXI', 'FINISH')

Обработка районов: 100%|██████████████████████| 140/140 [08:22<00:00,  3.59s/it]


In [24]:
carsharing_start = get_df("2024-01-01", "2025-01-01", 'CARSHARING', 'START')

Обработка районов: 100%|██████████████████████| 140/140 [05:11<00:00,  2.22s/it]


In [25]:
carsharing_finish = get_df("2024-01-01", "2025-01-01", 'CARSHARING', 'FINISH')

Обработка районов: 100%|██████████████████████| 140/140 [04:40<00:00,  2.00s/it]


## Обработка данных

In [30]:
taxi_start.rename(columns={'rideCount': 'taxi_start_rideCount'}, inplace=True)
taxi_finish.rename(columns={'rideCount': 'taxi_finish_rideCount'}, inplace=True)
carsharing_start.rename(columns={'rideCount': 'carsharing_start_rideCount'}, inplace=True)
carsharing_finish.rename(columns={'rideCount': 'carsharing_finish_rideCount'}, inplace=True)

In [32]:
taxi_start.drop(columns=['__typename'], inplace=True)
taxi_finish.drop(columns=['__typename'], inplace=True)
carsharing_start.drop(columns=['__typename'], inplace=True)
carsharing_finish.drop(columns=['__typename'], inplace=True)

In [34]:
taxi_start['timestamp'] = pd.to_datetime(taxi_start['date']) + pd.to_timedelta(taxi_start['hour'], unit='h')
taxi_start.drop(columns=['date', 'hour'], inplace=True)

taxi_finish['timestamp'] = pd.to_datetime(taxi_finish['date']) + pd.to_timedelta(taxi_finish['hour'], unit='h')
taxi_finish.drop(columns=['date', 'hour'], inplace=True)

carsharing_start['timestamp'] = pd.to_datetime(carsharing_start['date']) + pd.to_timedelta(carsharing_start['hour'], unit='h')
carsharing_start.drop(columns=['date', 'hour'], inplace=True)

carsharing_finish['timestamp'] = pd.to_datetime(carsharing_finish['date']) + pd.to_timedelta(carsharing_finish['hour'], unit='h')
carsharing_finish.drop(columns=['date', 'hour'], inplace=True)

In [35]:
carsharing_finish.sample(5)

carsharing_finish_rideCount           district_name  district_id  \
6063                         50.0     район Замоскворечье           94   
3013                         79.0         Басманный район          139   
2853                         40.0  Орехово-Борисово Южное           60   
4511                        181.0        район Коммунарка            8   
7911                         17.0           район Марфино           79   

               timestamp  
6063 2024-09-14 15:00:00  
3013 2024-05-08 12:00:00  
2853 2024-05-01 23:00:00  
4511 2024-07-09 21:00:00  
7911 2024-12-05 21:00:00

In [38]:
main_df = taxi_start.merge(taxi_finish, on=['district_id', 'district_name', 'timestamp'], how='outer')

In [39]:
main_df = main_df.merge(carsharing_start, on=['district_id', 'district_name', 'timestamp'], how='outer')

In [41]:
main_df = main_df.merge(carsharing_finish, on=['district_id', 'district_name', 'timestamp'], how='outer')

In [44]:
main_df.head()

taxi_start_rideCount  district_name  district_id           timestamp  \
0                   8.0  район Кунцево            0 2024-01-01 00:00:00   
1                  11.0  район Кунцево            0 2024-01-01 01:00:00   
2                   7.0  район Кунцево            0 2024-01-01 02:00:00   
3                  12.0  район Кунцево            0 2024-01-01 03:00:00   
4                   5.0  район Кунцево            0 2024-01-01 04:00:00   

   taxi_finish_rideCount  carsharing_start_rideCount  \
0                    4.0                         NaN   
1                   11.0                         1.0   
2                    7.0                         NaN   
3                    8.0                         NaN   
4                    6.0                         NaN   

   carsharing_finish_rideCount  
0                          NaN  
1                          1.0  
2                          NaN  
3                          NaN  
4                          NaN

In [46]:
main_df[['taxi_start_rideCount', 'taxi_finish_rideCount', 'carsharing_start_rideCount', 'carsharing_finish_rideCount']] = main_df[['taxi_start_rideCount', 'taxi_finish_rideCount', 'carsharing_start_rideCount', 'carsharing_finish_rideCount']].fillna(0)

In [48]:
main_df.groupby(['district_id']).timestamp.count()

district_id
0      8617
1      8715
2      8703
3      8257
4      4356
       ... 
135    8716
136    8714
137    8692
138    8693
139    8714
Name: timestamp, Length: 140, dtype: int64

In [52]:
main_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1185458 entries, 0 to 1185457
Data columns (total 7 columns):
 #   Column                       Non-Null Count    Dtype         
---  ------                       --------------    -----         
 0   taxi_start_rideCount         1185458 non-null  float64       
 1   district_name                1185458 non-null  object        
 2   district_id                  1185458 non-null  int64         
 3   timestamp                    1185458 non-null  datetime64[ns]
 4   taxi_finish_rideCount        1185458 non-null  float64       
 5   carsharing_start_rideCount   1185458 non-null  float64       
 6   carsharing_finish_rideCount  1185458 non-null  float64       
dtypes: datetime64[ns](1), float64(4), int64(1), object(1)
memory usage: 63.3+ MB


In [54]:
main_df['timestamp'] = pd.to_datetime(main_df['timestamp'])

full_range = pd.date_range(start=main_df['timestamp'].min(), 
                           end=main_df['timestamp'].max(), 
                           freq='H')

districts = main_df[['district_name', 'district_id']].drop_duplicates()

full_df = (districts.assign(key=1)
           .merge(pd.DataFrame({'timestamp': full_range, 'key': 1}), on='key')
           .drop(columns='key'))

df_filled = (full_df.merge(main_df, 
                           on=['timestamp', 'district_name', 'district_id'], 
                           how='left')
                    .fillna(0))


In [56]:
df_filled

district_name  district_id           timestamp  \
0          район Кунцево            0 2024-01-01 00:00:00   
1          район Кунцево            0 2024-01-01 01:00:00   
2          район Кунцево            0 2024-01-01 02:00:00   
3          район Кунцево            0 2024-01-01 03:00:00   
4          район Кунцево            0 2024-01-01 04:00:00   
...                  ...          ...                 ...   
1233115  Басманный район          139 2025-01-01 19:00:00   
1233116  Басманный район          139 2025-01-01 20:00:00   
1233117  Басманный район          139 2025-01-01 21:00:00   
1233118  Басманный район          139 2025-01-01 22:00:00   
1233119  Басманный район          139 2025-01-01 23:00:00   

         taxi_start_rideCount  taxi_finish_rideCount  \
0                         8.0                    4.0   
1                        11.0                   11.0   
2                         7.0                    7.0   
3                        12.0                    8.0   
4                         5.0                    6.0   
...                       ...                    ...   
1233115                 500.0                  525.0   
1233116                 544.0                  541.0   
1233117                 469.0                  505.0   
1233118                 516.0                  403.0   
1233119                 528.0                  394.0   

         carsharing_start_rideCount  carsharing_finish_rideCount  
0                               0.0                          0.0  
1                               1.0                          1.0  
2                               0.0                          0.0  
3                               0.0                          0.0  
4                               0.0                          0.0  
...                             ...                          ...  
1233115                        49.0                         38.0  
1233116                        40.0                         41.0  
1233117                        46.0                         42.0  
1233118                        27.0                         26.0  
1233119                        20.0                         17.0  

[1233120 rows x 7 columns]

In [58]:
df_filled.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1233120 entries, 0 to 1233119
Data columns (total 7 columns):
 #   Column                       Non-Null Count    Dtype         
---  ------                       --------------    -----         
 0   district_name                1233120 non-null  object        
 1   district_id                  1233120 non-null  int64         
 2   timestamp                    1233120 non-null  datetime64[ns]
 3   taxi_start_rideCount         1233120 non-null  float64       
 4   taxi_finish_rideCount        1233120 non-null  float64       
 5   carsharing_start_rideCount   1233120 non-null  float64       
 6   carsharing_finish_rideCount  1233120 non-null  float64       
dtypes: datetime64[ns](1), float64(4), int64(1), object(1)
memory usage: 65.9+ MB


In [60]:
# Проверка что количество регионов бьется с википедией

df_filled.district_name.nunique()

132

## Добавление координат

Источник данных
**Источник:** [Overpass Turbo](https://overpass-turbo.eu/)

---
Запрос на центры районов Москвы
```overpass
[out:json];
area[name="Москва"]->.moscow;
relation["admin_level"="8"](area.moscow);
out center tags;
```
Экспорт geojson, название файла - export_centers.geojson

In [62]:
df_filled.head()

district_name  district_id           timestamp  taxi_start_rideCount  \
0  район Кунцево            0 2024-01-01 00:00:00                   8.0   
1  район Кунцево            0 2024-01-01 01:00:00                  11.0   
2  район Кунцево            0 2024-01-01 02:00:00                   7.0   
3  район Кунцево            0 2024-01-01 03:00:00                  12.0   
4  район Кунцево            0 2024-01-01 04:00:00                   5.0   

   taxi_finish_rideCount  carsharing_start_rideCount  \
0                    4.0                         0.0   
1                   11.0                         1.0   
2                    7.0                         0.0   
3                    8.0                         0.0   
4                    6.0                         0.0   

   carsharing_finish_rideCount  
0                          0.0  
1                          1.0  
2                          0.0  
3                          0.0  
4                          0.0

In [654]:
response_centeres = requests.get(path_centers)
data_centeres = response_centeres.json()

df = pd.json_normalize(data_centeres['features'])
df.head()

type               id   properties.@id properties.addr:country  \
0  Feature  relation/226927  relation/226927                      RU   
1  Feature  relation/240229  relation/240229                      RU   
2  Feature  relation/364001  relation/364001                     NaN   
3  Feature  relation/364551  relation/364551                      RU   
4  Feature  relation/380704  relation/380704                     NaN   

  properties.addr:region properties.admin_level  \
0                 Москва                      8   
1                 Москва                      8   
2                    NaN                      8   
3                    NaN                      8   
4                    NaN                      8   

              properties.alt_name properties.boundary  \
0     муниципальный округ Кунцево      administrative   
1  муниципальный округ Крылатское      administrative   
2   муниципальный округ Мещанский      administrative   
3  муниципальный округ Сокольники      administrative   
4                             NaN      administrative   

                              properties.description   properties.name  ...  \
0  район — административно-территориальная единиц...     район Кунцево  ...   
1  район — административно-территориальная единиц...  район Крылатское  ...   
2  район — административно-территориальная единиц...   Мещанский район  ...   
3  район — административно-территориальная единиц...  район Сокольники  ...   
4                                                NaN  район Коммунарка  ...   

  properties.name:de properties.population properties.name:it  \
0                NaN                   NaN                NaN   
1                NaN                   NaN                NaN   
2                NaN                   NaN                NaN   
3                NaN                   NaN                NaN   
4                NaN                   NaN                NaN   

  properties.name:pt properties.contact:website properties.name:zh  \
0                NaN                        NaN                NaN   
1                NaN                        NaN                NaN   
2                NaN                        NaN                NaN   
3                NaN                        NaN                NaN   
4                NaN                        NaN                NaN   

  properties.name:zh-Hans properties.name:zh-Hant properties.name:vi  \
0                     NaN                     NaN                NaN   
1                     NaN                     NaN                NaN   
2                     NaN                     NaN                NaN   
3                     NaN                     NaN                NaN   
4                     NaN                     NaN                NaN   

  properties.loc_name  
0                 NaN  
1                 NaN  
2                 NaN  
3                 NaN  
4                 NaN  

[5 rows x 37 columns]

In [66]:
df.columns

Index(['type', 'id', 'properties.@id', 'properties.addr:country',
       'properties.addr:region', 'properties.admin_level',
       'properties.alt_name', 'properties.boundary', 'properties.description',
       'properties.name', 'properties.name:ca', 'properties.name:en',
       'properties.name:ru', 'properties.name:uk',
       'properties.official_status', 'properties.type', 'properties.wikidata',
       'properties.wikipedia', 'properties.@geometry', 'geometry.type',
       'geometry.coordinates', 'properties.name:be', 'properties.omkmo:code',
       'properties.omkte:code', 'properties.name:eo', 'properties.website',
       'properties.image', 'properties.name:de', 'properties.population',
       'properties.name:it', 'properties.name:pt',
       'properties.contact:website', 'properties.name:zh',
       'properties.name:zh-Hans', 'properties.name:zh-Hant',
       'properties.name:vi', 'properties.loc_name'],
      dtype='object')

In [68]:
df_main = df[['properties.name', 'geometry.coordinates']]

In [70]:
df_main = df_main.copy()
df_main['lat'] = df_main['geometry.coordinates'].apply(lambda x: x[1])
df_main['lon'] = df_main['geometry.coordinates'].apply(lambda x: x[0])
df_main.drop(columns=['geometry.coordinates'], inplace=True)

In [72]:
df_main.head()

properties.name        lat        lon
0     район Кунцево  55.758995  37.167845
1  район Крылатское  55.761077  37.415025
2   Мещанский район  55.778081  37.628645
3  район Сокольники  55.803140  37.677806
4  район Коммунарка  55.567655  37.461537

In [74]:
df_main.columns = ['district_name', 'lat', 'lon']

In [76]:
df_with_coords = df_filled.merge(df_main, how='left', on='district_name')

In [78]:
df_with_coords.sample(10)

district_name  district_id           timestamp  \
120431            район Строгино           13 2024-09-03 23:00:00   
1188329           район Бекасово          134 2024-12-01 17:00:00   
987317       Ломоносовский район          112 2024-02-04 05:00:00   
510042   район Нагатинский Затон           57 2024-11-28 18:00:00   
1114323          район Измайлово          126 2024-07-07 03:00:00   
1083570        район Богородское          123 2024-01-08 18:00:00   
684929            район Свиблово           77 2024-10-06 17:00:00   
1154710          район Матушкино          131 2024-02-05 22:00:00   
297888         Хорошёвский район           33 2024-10-28 00:00:00   
43762              район Кунцево            4 2024-12-21 10:00:00   

         taxi_start_rideCount  taxi_finish_rideCount  \
120431                  174.0                  222.0   
1188329                  21.0                   24.0   
987317                    0.0                    0.0   
510042                  187.0                  240.0   
1114323                 143.0                  191.0   
1083570                 251.0                  250.0   
684929                  275.0                  250.0   
1154710                   0.0                    0.0   
297888                  221.0                  214.0   
43762                     0.0                    0.0   

         carsharing_start_rideCount  carsharing_finish_rideCount        lat  \
120431                         28.0                         35.0  55.800036   
1188329                         5.0                          4.0  55.413924   
987317                          0.0                          0.0  55.679074   
510042                         29.0                         43.0  55.675456   
1114323                        11.0                         12.0  55.781239   
1083570                        37.0                         49.0  55.820041   
684929                         91.0                         77.0  55.853074   
1154710                         0.0                          0.0  56.002800   
297888                         21.0                         26.0  55.781791   
43762                           0.0                          0.0  55.758995   

               lon  
120431   37.407437  
1188329  36.958104  
987317   37.533612  
510042   37.682934  
1114323  37.774260  
1083570  37.708070  
684929   37.648492  
1154710  37.205145  
297888   37.529425  
43762    37.167845

## Добавление данных о погоде

In [80]:
df_with_coords.head()

district_name  district_id           timestamp  taxi_start_rideCount  \
0  район Кунцево            0 2024-01-01 00:00:00                   8.0   
1  район Кунцево            0 2024-01-01 01:00:00                  11.0   
2  район Кунцево            0 2024-01-01 02:00:00                   7.0   
3  район Кунцево            0 2024-01-01 03:00:00                  12.0   
4  район Кунцево            0 2024-01-01 04:00:00                   5.0   

   taxi_finish_rideCount  carsharing_start_rideCount  \
0                    4.0                         0.0   
1                   11.0                         1.0   
2                    7.0                         0.0   
3                    8.0                         0.0   
4                    6.0                         0.0   

   carsharing_finish_rideCount        lat        lon  
0                          0.0  55.758995  37.167845  
1                          1.0  55.758995  37.167845  
2                          0.0  55.758995  37.167845  
3                          0.0  55.758995  37.167845  
4                          0.0  55.758995  37.167845

In [82]:
df_with_coords.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1233120 entries, 0 to 1233119
Data columns (total 9 columns):
 #   Column                       Non-Null Count    Dtype         
---  ------                       --------------    -----         
 0   district_name                1233120 non-null  object        
 1   district_id                  1233120 non-null  int64         
 2   timestamp                    1233120 non-null  datetime64[ns]
 3   taxi_start_rideCount         1233120 non-null  float64       
 4   taxi_finish_rideCount        1233120 non-null  float64       
 5   carsharing_start_rideCount   1233120 non-null  float64       
 6   carsharing_finish_rideCount  1233120 non-null  float64       
 7   lat                          1233120 non-null  float64       
 8   lon                          1233120 non-null  float64       
dtypes: datetime64[ns](1), float64(6), int64(1), object(1)
memory usage: 84.7+ MB


In [84]:
# Переводим столбец timestamp в формат datetime
df_with_coords["timestamp"] = pd.to_datetime(df_with_coords["timestamp"])

# Получаем уникальные пары координат
unique_points = df_with_coords[["lat", "lon"]].drop_duplicates()

# Словарь для хранения погодных данных по координатам
weather_data_all = []

start = df_with_coords["timestamp"].min()
end = df_with_coords["timestamp"].max()

# Получаем погодные данные для каждой уникальной точки
for _, row in tqdm(unique_points.iterrows(), total=len(unique_points)):
    point = Point(row["lat"], row["lon"])
    data = Hourly(point, start, end).fetch().reset_index()
    
    # Добавляем координаты для последующего объединения
    data["lat"] = row["lat"]
    data["lon"] = row["lon"]
    
    # Оставляем только нужные столбцы
    data = data[["time", "lat", "lon", "temp", "prcp", "rhum", "wspd", "coco"]]
    data = data.rename(columns={"time": "timestamp"})
    
    weather_data_all.append(data)

# Объединяем все погодные данные в один датафрейм
weather_df = pd.concat(weather_data_all, ignore_index=True)

100%|█████████████████████████████████████████| 132/132 [00:15<00:00,  8.70it/s]


In [86]:
weather_df

timestamp        lat        lon  temp  prcp  rhum  wspd  \
0       2024-01-01 00:00:00  55.758995  37.167845 -11.0   0.0  79.0  21.6   
1       2024-01-01 01:00:00  55.758995  37.167845 -11.0   0.0  79.0  18.0   
2       2024-01-01 02:00:00  55.758995  37.167845 -11.0   0.0  79.0  21.6   
3       2024-01-01 03:00:00  55.758995  37.167845 -11.0   0.0  79.0  21.6   
4       2024-01-01 04:00:00  55.758995  37.167845 -11.0   0.0  79.0  18.0   
...                     ...        ...        ...   ...   ...   ...   ...   
1162651 2025-01-01 19:00:00  55.766398  37.670699   1.4   0.1  92.0   3.7   
1162652 2025-01-01 20:00:00  55.766398  37.670699   1.6   0.0  91.0   3.7   
1162653 2025-01-01 21:00:00  55.766398  37.670699   1.4   0.0  91.0   7.0   
1162654 2025-01-01 22:00:00  55.766398  37.670699   1.6   0.0  91.0   7.4   
1162655 2025-01-01 23:00:00  55.766398  37.670699   1.9   0.0  90.0   5.5   

         coco  
0         3.0  
1         3.0  
2         3.0  
3         3.0  
4         3.0  
...       ...  
1162651  12.0  
1162652  10.0  
1162653   7.0  
1162654  10.0  
1162655  10.0  

[1162656 rows x 8 columns]

In [393]:
ready_df = df_with_coords.merge(weather_df, how='left', on=["timestamp", "lat", "lon"])


## Обработка названий полей и пропусков в погодных данных

In [396]:
ready_df.rename(columns={'temp': 'temperature', 
                         'prcp': 'precipitation', 
                         'rhum': 'humidity',
                         'wspd': 'wind_speed',
                         'taxi_start_rideCount': 'n_taxi_start',
                         'taxi_finish_rideCount': 'n_taxi_end',
                         'carsharing_start_rideCount': 'n_carsharing_start',
                         'carsharing_finish_rideCount': 'n_carsharing_end',
                        'coco': 'weather_code'
                        }, inplace=True)

In [398]:
# задал порядок полей

ready_df = ready_df[['timestamp', 'district_name', 'district_id', 'lat', 'lon', 'n_taxi_start', 'n_taxi_end', \
'n_carsharing_start','n_carsharing_end', 'temperature','precipitation','humidity','wind_speed','weather_code']]

In [400]:
ready_df.sample(10)

timestamp           district_name  district_id        lat  \
192132 2024-10-25 12:00:00     Тимирязевский район           21  55.827299   
674899 2024-08-16 19:00:00      Алексеевский район           76  55.811320   
223407 2024-05-13 15:00:00             район Сокол           25  55.803209   
947209 2024-07-17 01:00:00      Южнопортовый район          107  55.714529   
753365 2024-07-14 05:00:00  район Косино-Ухтомский           85  55.713929   
438789 2024-10-26 21:00:00        Ново-Переделкино           49  55.641910   
365946 2024-07-19 18:00:00          район Бибирево           41  55.896366   
226468 2024-09-18 04:00:00             район Сокол           25  55.803209   
584973 2024-05-31 21:00:00   район Выхино-Жулебино           66  55.698332   
910255 2024-05-06 07:00:00         Таганский район          103  55.740297   

              lon  n_taxi_start  n_taxi_end  n_carsharing_start  \
192132  37.558254         377.0       412.0                47.0   
674899  37.652847         401.0       357.0                77.0   
223407  37.503648         249.0       216.0                38.0   
947209  37.680478         123.0       115.0                19.0   
753365  37.890837          55.0        86.0                 8.0   
438789  37.374155         180.0       213.0                38.0   
365946  37.615372         226.0       252.0                45.0   
226468  37.503648          22.0        14.0                 7.0   
584973  37.825991         532.0       614.0                97.0   
910255  37.665955         340.0       389.0                43.0   

        n_carsharing_end  temperature  precipitation  humidity  wind_speed  \
192132              31.0          6.9            0.0      61.0         7.0   
674899              51.0         17.4            0.0      74.0         0.0   
223407              17.0          8.1            0.0      43.0         4.0   
947209              20.0         19.9            0.0      91.0         0.0   
753365               6.0         24.7            0.0      72.0         1.8   
438789              35.0          7.0            0.0      93.0        14.0   
365946              44.0         19.2            0.0      90.0         0.0   
226468               4.0         12.5            0.0      83.0         0.0   
584973             107.0         16.4            0.0      94.0         0.0   
910255              72.0          8.1            0.0      53.0         3.7   

        weather_code  
192132           3.0  
674899           2.0  
223407           3.0  
947209           1.0  
753365          17.0  
438789           5.0  
365946           3.0  
226468           1.0  
584973           2.0  
910255           3.0

In [402]:
ready_df.isnull().sum()

timestamp                 0
district_name             0
district_id               0
lat                       0
lon                       0
n_taxi_start              0
n_taxi_end                0
n_carsharing_start        0
n_carsharing_end          0
temperature               0
precipitation         33780
humidity                  0
wind_speed                0
weather_code           2523
dtype: int64

In [404]:
# Пропуски были по timestamp, а не по координатам, поэтому заполнил последним известным precipitation
ready_df['precipitation'] = ready_df['precipitation'].ffill()

In [406]:
ready_df['weather_code'] = ready_df['weather_code'].ffill()

In [408]:
# ready_df.to_csv('main_df.csv', index=False)

## Выделение новых временных признаков 

In [413]:
ready_df.head()

timestamp  district_name  district_id        lat        lon  \
0 2024-01-01 00:00:00  район Кунцево            0  55.758995  37.167845   
1 2024-01-01 01:00:00  район Кунцево            0  55.758995  37.167845   
2 2024-01-01 02:00:00  район Кунцево            0  55.758995  37.167845   
3 2024-01-01 03:00:00  район Кунцево            0  55.758995  37.167845   
4 2024-01-01 04:00:00  район Кунцево            0  55.758995  37.167845   

   n_taxi_start  n_taxi_end  n_carsharing_start  n_carsharing_end  \
0           8.0         4.0                 0.0               0.0   
1          11.0        11.0                 1.0               1.0   
2           7.0         7.0                 0.0               0.0   
3          12.0         8.0                 0.0               0.0   
4           5.0         6.0                 0.0               0.0   

   temperature  precipitation  humidity  wind_speed  weather_code  
0        -11.0            0.0      79.0        21.6           3.0  
1        -11.0            0.0      79.0        18.0           3.0  
2        -11.0            0.0      79.0        21.6           3.0  
3        -11.0            0.0      79.0        21.6           3.0  
4        -11.0            0.0      79.0        18.0           3.0

In [427]:
# Категориальный признак утренний / вечерний час пик
def classify_rush_hour(timestamp):
    hour = timestamp.hour
    if 7 <= hour < 10:
        return 1
    elif 17 <= hour < 20:
        return 2
    else:
        return 0

In [429]:
ready_df['rush_hour'] = ready_df['timestamp'].apply(classify_rush_hour)

In [433]:
def get_season(timestamp):
    month = timestamp.month
    if month in [12, 1, 2]:
        return 0  # Зима
    elif month in [3, 4, 5]:
        return 1  # Весна
    elif month in [6, 7, 8]:
        return 2  # Лето
    else:
        return 3  # Осень

In [439]:
ready_df['season'] = ready_df['timestamp'].apply(get_season)

In [449]:
# Убрал 1 января 2025, чтобы не было ошибок с другими признаками

ready_df = ready_df[ready_df['timestamp'].dt.year == 2024]

In [451]:
# Российские праздники
russian_holidays = [
    "2024-01-01", "2024-01-02", "2024-01-03", "2024-01-04", "2024-01-05", "2024-01-06", "2024-01-07", "2024-01-08",  # Новогодние праздники и Рождество
    "2024-02-23",  # День защитника Отечества
    "2024-03-08",  # Международный женский день
    "2024-05-01",  # Праздник Весны и Труда
    "2024-05-09",  # День Победы
    "2024-05-10",  # День Победы
    "2024-06-12",  # День России
    "2024-11-04",  # Новогодние праздники
    "2024-12-30",  # Новогодние праздники
    "2024-12-31",  # Новогодние праздники
]
russian_holidays = pd.to_datetime(russian_holidays)

In [489]:
def is_holiday_or_weekend(timestamp):
    return 1 if (timestamp.weekday() >= 5 or timestamp.date() in russian_holidays.date) else 0

In [499]:
ready_df['is_holiday_or_weekend'] = ready_df['timestamp'].apply(is_holiday_or_weekend)

In [501]:
ready_df.sample(5)

timestamp          district_name  district_id        lat  \
1092819 2024-01-27 03:00:00     район Метрогородок          124  55.843718   
865584  2024-04-10 00:00:00  район Северное Бутово           98  55.568052   
965713  2024-08-23 01:00:00    Академический район          109  55.689537   
839712  2024-05-03 00:00:00        район Хамовники           95  55.730338   
940240  2024-10-01 16:00:00        район Лефортово          106  55.754333   

               lon  n_taxi_start  n_taxi_end  n_carsharing_start  \
1092819  37.727534          34.0        51.0                 3.0   
865584   37.570211         126.0       116.0                18.0   
965713   37.576881         104.0       143.0                14.0   
839712   37.576639         295.0       166.0                14.0   
940240   37.703555         420.0       334.0                89.0   

         n_carsharing_end  temperature  precipitation  humidity  wind_speed  \
1092819               1.0         -5.6            0.0      91.0         4.0   
865584               15.0         11.0            0.0      88.0         7.2   
965713               14.0         17.5            0.0      68.0         1.8   
839712               17.0          5.5            0.0      60.0        11.0   
940240               66.0         14.2            0.0      64.0         3.7   

         weather_code  rush_hour  season  is_holiday_or_weekend  
1092819          14.0          0       0                      1  
865584            1.0          0       1                      0  
965713            2.0          0       2                      0  
839712            3.0          0       1                      0  
940240            1.0          0       3                      0

In [ ]:
# ready_df.to_csv('main_df.csv', index=False)

## Добавление данных о загруженности метро 

In [544]:
metro = pd.read_csv(path_stations)

In [546]:
metro = metro[metro['Year'] == 2024]

In [548]:
metro

Year     Quarter        NameOfStation                             Line  \
3427  2024   I квартал         Авиамоторная          Большая кольцевая линия   
3428  2024   I квартал         Авиамоторная                Калининская линия   
3429  2024   I квартал        Автозаводская             Замоскворецкая линия   
3430  2024   I квартал        Автозаводская    Московское центральное кольцо   
3431  2024   I квартал        Академическая           Калужско-Рижская линия   
...    ...         ...                  ...                              ...   
4639  2024  IV квартал         Юго-Западная             Сокольническая линия   
4640  2024  IV квартал                Южная  Серпуховско-Тимирязевская линия   
4641  2024  IV квартал              Ясенево           Калужско-Рижская линия   
4642  2024  IV квартал            Яхромская      Люблинско-Дмитровская линия   
4643  2024  IV квартал  Улица дмитриевского               Некрасовская линия   

      StationLoad   Latitude  Longitude  
3427            1  55.751933  37.717444  
3428            1  55.751933  37.717444  
3429            1  55.706634  37.657008  
3430            2  55.706634  37.657008  
3431            2  55.687147  37.572300  
...           ...        ...        ...  
4639            1  55.663146  37.482852  
4640            5  55.622436  37.609047  
4641            5  55.606182  37.533400  
4642            5  55.879904  37.545429  
4643            4  55.710311  37.879045  

[1217 rows x 7 columns]

In [550]:
metro_coords = metro[['Latitude', 'Longitude']].drop_duplicates()

In [552]:
# Ищу район через координаты по геокодеру

import pandas as pd
from geopy.geocoders import Nominatim
from geopy.exc import GeocoderTimedOut
from tqdm import tqdm
import time

# Инициализация геокодера
geolocator = Nominatim(user_agent="moscow_schools")

def get_district(lat, lon):
    """Получить район по координатам через Nominatim (OSM)."""
    try:
        time.sleep(1)
        location = geolocator.reverse((lat, lon), language="ru", exactly_one=True)
        if location and 'address' in location.raw:
            address = location.raw['address']
            district = address.get('suburb') or address.get('city_district') or address.get('borough')
            return district
        return None
    except:
        time.sleep(10)
        return get_district(lat, lon)

tqdm.pandas()
metro_coords['district'] = metro_coords.progress_apply(lambda row: get_district(row['Latitude'], row['Longitude']), axis=1)

100%|█████████████████████████████████████████| 261/261 [05:17<00:00,  1.22s/it]


In [512]:
metro.sample(5)

Year      Quarter   NameOfStation                           Line  \
458   2024   II квартал  Новохохловская  Московское центральное кольцо   
762   2024  III квартал  Новоясеневская         Калужско-Рижская линия   
440   2024   II квартал     Москва-Сити  Московское центральное кольцо   
82    2024    I квартал        Киевская                Кольцевая линия   
1114  2024   IV квартал   Проспект мира                Кольцевая линия   

      StationLoad   Latitude  Longitude             district Start_Timestamp  \
458             3  55.723889  37.716111  Нижегородский район      2024-04-01   
762             5  55.601947  37.553017        район Ясенево      2024-07-01   
440             1  55.748324  37.533282    Пресненский район      2024-04-01   
82              4  55.743117  37.564132   район Дорогомилово      2024-01-01   
1114            1  55.779584  37.633646      Мещанский район      2024-10-01   

     End_Timestamp  
458     2024-06-30  
762     2024-09-30  
440     2024-06-30  
82      2024-03-31  
1114    2024-12-31

In [594]:
# Для каких станций не определился район

metro_coords[metro_coords.district.isna()]

Empty DataFrame
Columns: [Latitude, Longitude, district]
Index: []

In [556]:
# Присваиваю вручную значения станций метро

metro_coords.at[3442, "district"] = "район Внуково"

In [558]:
metro_coords.at[3521, "district"] = "район Выхино-Жулебино"

In [560]:
metro_coords.at[3581, "district"] = "район Коммунарка"

In [562]:
metro_coords.at[3594, "district"] = "район Коммунарка"

In [564]:
metro_coords.at[3622, "district"] = "район Коммунарка"

In [566]:
metro_coords.at[3630, "district"] = "район Внуково"

In [568]:
metro_coords.at[3633, "district"] = "район Внуково"

In [592]:
metro_coords.at[3639, "district"] = "район Коммунарка"

In [570]:
metro_coords.at[3643, "district"] = "район Коммунарка"

In [572]:
metro_coords.at[3696, "district"] = "район Коммунарка"

In [574]:
metro_coords.at[4224, "district"] = "район Коммунарка"

In [576]:
metro_coords.at[4425, "district"] = "район Коммунарка"

In [578]:
metro_coords.at[4430, "district"] = "район Коммунарка"

In [580]:
# Проверяю на несовпадения названий районов метро и районов основого датасета
for d in metro_coords.district.unique():
    if d in ready_df.district_name.unique():
        continue
    else:
        print(d)

Бауманка
Гавриково
Чернево
район Орехово-Борисово Южное
Кожухово
Канатчиково
Дмитровский
Черкизово
Павшинская Пойма
Восход
None


In [582]:
sorted(ready_df.district_name.unique())

['Академический район',
 'Алексеевский район',
 'Алтуфьевский район',
 'Бабушкинский район',
 'Басманный район',
 'Бескудниковский район',
 'Бутырский район',
 'Войковский район',
 'Гагаринский район',
 'Головинский район',
 'Даниловский район',
 'Дмитровский район',
 'Донской район',
 'Краснопахорский район',
 'Красносельский район',
 'Ломоносовский район',
 'Лосиноостровский район',
 'Мещанский район',
 'Можайский район',
 'Молжаниновский район',
 'Нагорный район',
 'Нижегородский район',
 'Ново-Переделкино',
 'Обручевский район',
 'Орехово-Борисово Южное',
 'Останкинский район',
 'Пресненский район',
 'Рязанский район',
 'Савёловский район',
 'Таганский район',
 'Тверской район',
 'Тимирязевский район',
 'Тропарёво-Никулино',
 'Филимонковский район',
 'Хорошёвский район',
 'Южнопортовый район',
 'Ярославский район',
 'район Арбат',
 'район Аэропорт',
 'район Беговой',
 'район Бекасово',
 'район Бибирево',
 'район Бирюлёво Восточное',
 'район Бирюлёво Западное',
 'район Богородское',

In [584]:
to_rename = {
    'Бауманка': 'Басманный район',
    'Гавриково': 'район Южное Бутово', 
    'Чернево': 'район Южное Бутово',
    'район Орехово-Борисово Южное': 'Орехово-Борисово Южное', 
    'Кожухово': 'район Косино-Ухтомский', 
    'Канатчиково': 'Донской район',
    'Дмитровский': 'Дмитровский район',
    'Черкизово':  'Молжаниновский район',
    'Павшинская Пойма': 'Митино',
    'Восход': 'район Левобережный',
    'Митино': 'район Митино'
}
    

In [598]:
# Переименовываю несовпадения в названиях районов для объединения

metro_coords.district = metro_coords.district.apply(lambda x: to_rename[x] if x in to_rename.keys() else x)

In [600]:
# Проверяю на несовпадения названий районов метро и районов основого датасета
for d in metro_coords.district.unique():
    if d in ready_df.district_name.unique():
        continue
    else:
        print(d)

In [604]:
metro_coords.sample(5)

Latitude  Longitude             district
3528  55.756842  37.408139     район Крылатское
3519  55.839637  37.520037        район Коптево
3684  55.618730  37.505912        район Ясенево
3575  55.731835  37.729404  Нижегородский район
3578  55.752237  37.814587    район Новогиреево

In [606]:
metro = pd.merge(metro, metro_coords, how='left', on=['Latitude', 'Longitude'])

In [608]:
metro.head()

Year    Quarter  NameOfStation                           Line  StationLoad  \
0  2024  I квартал   Авиамоторная        Большая кольцевая линия            1   
1  2024  I квартал   Авиамоторная              Калининская линия            1   
2  2024  I квартал  Автозаводская           Замоскворецкая линия            1   
3  2024  I квартал  Автозаводская  Московское центральное кольцо            2   
4  2024  I квартал  Академическая         Калужско-Рижская линия            2   

    Latitude  Longitude             district  
0  55.751933  37.717444      район Лефортово  
1  55.751933  37.717444      район Лефортово  
2  55.706634  37.657008    Даниловский район  
3  55.706634  37.657008    Даниловский район  
4  55.687147  37.572300  Академический район

In [612]:
group_metro = metro.groupby(['district', 'Quarter'], as_index=False).StationLoad.sum()

In [624]:
group_metro.sample(5)

district      Quarter  StationLoad
132            район Богородское    I квартал            9
117            Ярославский район   II квартал            4
88               Рязанский район    I квартал            7
64           Нижегородский район    I квартал            7
372  район Чертаново Центральное  III квартал            3

In [626]:
group_metro.columns = ['district_name', 'quarter', 'station_load']

In [618]:
# Добавлю квартал в основной датасет
def get_quarter(timestamp):
    month = timestamp.month
    if month in [1, 2, 3]:
        return "I квартал"
    elif month in [4, 5, 6]:
        return "II квартал"
    elif month in [7, 8, 9]:
        return "III квартал"
    else:
        return "IV квартал"

In [620]:
ready_df['quarter'] = ready_df['timestamp'].apply(get_quarter)

In [622]:
ready_df.sample(5)

timestamp       district_name  district_id        lat  \
905835 2024-11-05 03:00:00   Пресненский район          102  55.759959   
822049 2024-05-01 01:00:00     район Восточный           93  55.906955   
674208 2024-07-19 00:00:00  Алексеевский район           76  55.811320   
547880 2024-03-15 08:00:00      район Братеево           62  55.632697   
918315 2024-04-05 03:00:00      район Якиманка          104  55.730038   

              lon  n_taxi_start  n_taxi_end  n_carsharing_start  \
905835  37.561845         170.0       120.0                13.0   
822049  37.844685           4.0         8.0                 0.0   
674208  37.652847         161.0       197.0                29.0   
547880  37.760341         238.0       197.0                37.0   
918315  37.601996          71.0        23.0                 3.0   

        n_carsharing_end  temperature  precipitation  humidity  wind_speed  \
905835              11.0         -0.3            0.1      77.0         7.0   
822049               1.0         13.1            0.0      71.0         1.8   
674208              17.0         20.9            0.0      86.0         7.0   
547880              35.0          3.0            0.0      65.0        10.8   
918315               0.0         -2.1            0.0      68.0        11.0   

        weather_code  rush_hour  season  is_holiday_or_weekend      quarter  
905835           4.0          0       3                      0   IV квартал  
822049           4.0          0       1                      1   II квартал  
674208           3.0          0       2                      0  III квартал  
547880           3.0          1       1                      0    I квартал  
918315           3.0          0       1                      0   II квартал

In [628]:
ready_df.shape

(1229760, 18)

In [630]:
ready_df_metro = pd.merge(ready_df, group_metro, how='left', on=['district_name', 'quarter'])

In [632]:
ready_df_metro.shape

(1229760, 19)

In [634]:
ready_df_metro.sample(5)

timestamp                    district_name  district_id  \
1130396 2024-09-08 20:00:00                    район Крюково          128   
334473  2024-01-29 09:00:00            Бескудниковский район           38   
521720  2024-05-24 08:00:00  район Орехово-Борисово Северное           59   
584853  2024-07-31 21:00:00            район Выхино-Жулебино           66   
1228184 2024-10-27 08:00:00                  Басманный район          139   

               lat        lon  n_taxi_start  n_taxi_end  n_carsharing_start  \
1130396  55.973617  37.182440         319.0       364.0                21.0   
334473   55.863778  37.551715         236.0       300.0                18.0   
521720   55.621195  37.700828         307.0       224.0                34.0   
584853   55.698332  37.825991         479.0       631.0                95.0   
1228184  55.766398  37.670699         334.0       396.0                31.0   

         n_carsharing_end  temperature  precipitation  humidity  wind_speed  \
1130396              29.0         17.0            0.0      68.0         0.0   
334473               21.0         -2.9            0.0      84.0         4.0   
521720               34.0         18.0            0.0      30.0         7.2   
584853              116.0         15.1            0.0      93.0         4.0   
1228184              42.0          7.8            0.0      85.0         1.8   

         weather_code  rush_hour  season  is_holiday_or_weekend      quarter  \
1130396           1.0          0       3                      1  III квартал   
334473            4.0          1       0                      0    I квартал   
521720            1.0          1       1                      0   II квартал   
584853            3.0          0       2                      0  III квартал   
1228184           3.0          1       3                      1   IV квартал   

         station_load  
1130396           NaN  
334473           11.0  
521720            5.0  
584853           23.0  
1228184          12.0

In [636]:
ready_df_metro.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1229760 entries, 0 to 1229759
Data columns (total 19 columns):
 #   Column                 Non-Null Count    Dtype         
---  ------                 --------------    -----         
 0   timestamp              1229760 non-null  datetime64[ns]
 1   district_name          1229760 non-null  object        
 2   district_id            1229760 non-null  int64         
 3   lat                    1229760 non-null  float64       
 4   lon                    1229760 non-null  float64       
 5   n_taxi_start           1229760 non-null  float64       
 6   n_taxi_end             1229760 non-null  float64       
 7   n_carsharing_start     1229760 non-null  float64       
 8   n_carsharing_end       1229760 non-null  float64       
 9   temperature            1229760 non-null  float64       
 10  precipitation          1229760 non-null  float64       
 11  humidity               1229760 non-null  float64       
 12  wind_speed             12297

In [638]:
ready_df_metro.station_load = ready_df_metro.station_load.fillna(0)

In [640]:
ready_df_metro.to_csv('main_df.csv', index=False)

## Описание полей (неполное)

### Описание полей DataFrame о поездках такси и каршеринга по районам Москвы

- **`timestamp` (datetime64[ns])** — Метка времени, соответствующая периоду наблюдений.  
- **`district_name` (object)** — Название района Москвы.  
- **`district_id` (int64)** — Уникальный идентификатор района.  
- **`lat` (float64)** — Широта центра района.  
- **`lon` (float64)** — Долгота центра района.  
- **`n_taxi_start` (float64)** — Количество поездок на такси, начавшихся в районе.  
- **`n_taxi_end` (float64)** — Количество поездок на такси, завершившихся в районе.  
- **`n_carsharing_start` (float64)** — Количество поездок на каршеринге, начавшихся в районе.  
- **`n_carsharing_end` (float64)** — Количество поездок на каршеринге, завершившихся в районе.  
- **`temperature` (float64)** — Температура воздуха (°C) на момент наблюдений.  
- **`precipitation` (float64)** — Количество осадков (мм) на момент наблюдений.  
- **`humidity` (float64)** — Влажность воздуха (%) на момент наблюдений.  
- **`wind_speed` (float64)** — Скорость ветра (м/с) на момент наблюдений.  
- **`weather_code` (float64)** — Код типа погоды согласно метеоданным

Код состояния погоды (**weather_code**) в принимает значения от **1 до 25**, а также **NaN** для отсутствующих данных. Эти значения соответствуют различным погодным явлениям, таким как типы осадков, облачность, видимость и другие метеорологические явления:

| Код | Погодное условие         |
|-----|--------------------------|
| 1   | Ясно                    |
| 2   | Солнечно                 |
| 3   | Облачно                  |
| 4   | Пасмурно                 |
| 5   | Туман                    |
| 6   | Ледяной туман            |
| 7   | Легкий дождь             |
| 8   | Дождь                    |
| 9   | Сильный дождь            |
| 10  | Ледяной дождь            |
| 11  | Сильный ледяной дождь    |
| 12  | Дождь со снегом          |
| 13  | Сильный дождь со снегом  |
| 14  | Легкий снегопад          |
| 15  | Снегопад                 |
| 16  | Сильный снегопад         |
| 17  | Дождевой ливень          |
| 18  | Сильный дождевой ливень  |
| 19  | Дождь со снегом (ливень) |
| 20  | Сильный дождь со снегом  |
| 21  | Снежный ливень           |
| 22  | Сильный снежный ливень   |
| 23  | Молния                   |
| 24  | Град                     |
| 25  | Гроза                    |
| **NaN** | Нет данных           |
